# Identify the most likely language for each tweet

For this analyses I will explore the langid package in more detail in order to come up with the most likely language of a tweet.

Next to the regular language identification function in the langid package, the module also provides a function that returns the likelihood for each language in a text. For this analysis I will further explore the possibilities of this function.

In addition to the langid package, the column that states the country where the tweet was posted will also be used to select the most likely language out of all the possible languages that the function returns.

For this first iteration on the dataset, I will use only the information about the tweets and the country where the tweet was posted. 

#### Import and load the data

In [1]:
import pandas as pd
import numpy as np
import re
import langid

pd.set_option('display.max_colwidth', -1)
pd.set_option("display.max_rows", None)
pd.set_option('display.max_columns', None)

import warnings
warnings.filterwarnings('ignore')

In [2]:
# load data
T = pd.read_csv("all_annotated.tsv", sep = "\t")

In [3]:
print T.shape
T.head()

(10502, 10)


Tweet ID Country        Date  \
0  434215992731136000  TR      2014-02-14   
1  285903159434563584  TR      2013-01-01   
2  285948076496142336  NL      2013-01-01   
3  285965965118824448  US      2013-01-01   
4  286057979831275520  US      2013-01-01   

                                                                                    Tweet  \
0  Bugün bulusmami lazimdiii                                                                
1  Volkan konak adami tribe sokar yemin ederim :D                                           
2  Bed                                                                                      
3  I felt my first flash of violence at some fool who bumped into me.... I pity the fool.   
4  Ladies drink and get in free till 10:30                                                  

   Definitely English  Ambiguous  Definitely Not English  Code-Switched  \
0  0                   0          1                       0               
1  0                   0          1                       0               
2  1                   0          0                       0               
3  1                   0          0                       0               
4  1                   0          0                       0               

   Ambiguous due to Named Entities  Automatically Generated Tweets  
0  0                                0                               
1  0                                0                               
2  0                                0                               
3  0                                0                               
4  0                                0

### Compare regular language identifier with all possible identified languages

In [4]:
from langid.langid import LanguageIdentifier, model
identifier = LanguageIdentifier.from_modelstring(model, norm_probs=True)

In [5]:
# adjust how many languages to store with a threshold parameter 
# that stores only the languages with a confidence score that is no larger than x digits behind the comma.  
def language_confidence(text, threshold=6):
    language_conf = []
    for pair in identifier.rank(text):
        if round(pair[1], threshold) > 0.:
            language_conf.append(pair)    
    return language_conf

In [6]:
T['Tweet'][0:5].apply(identifier.classify)

0    (az, 0.856022267327)
1    (ms, 0.865002557468)
2    (en, 0.169461505959)
3    (en, 1.0)           
4    (en, 0.999613490658)
Name: Tweet, dtype: object

In [7]:
T['Tweet'][0:5].apply(lambda x: language_confidence(x, threshold=2))

0    [(az, 0.856022267327), (tr, 0.143677328034)]                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
1    [(ms, 0.865002557468), (id, 0.0997131200704), (tr, 0.0340997291609)]                                                                                                                                                              

### Remove tags and urls

In [8]:
# remove urls starting with http 
http = r'http\S+'
T['Tweet_stripped'] = T['Tweet'].str.replace(http, ' ' )

# remove tags
T['Tweet_stripped'] = T['Tweet_stripped'].apply(lambda x: ' '.join(word for word in x.split(' ')\
                                                                   if not word.startswith('@')))

### Create column for identified languages and confidence scores

In [9]:
T['language_conf'] = T['Tweet_stripped'].apply(lambda x: language_confidence(x, threshold=2)) 

### Find the most likely language

In [10]:
# convert country ISO codes to lower case
T['Country'] = T['Country'].str.lower()

In [11]:
# write function that returns the identified language only
def languages(text, threshold=6):
    language_conf = []
    for pair in identifier.rank(text):
        if round(pair[1], threshold) > 0.:
            language_conf.append(pair)    
    return [row[0] for row in language_conf]

T['language_only'] = T['Tweet_stripped'].apply(lambda x: languages(x, threshold=2))

In [12]:
# write function that returns the most likely language(s)
def tweet_language(row):
    if row.Country in row.language_only:
        return row.Country
    elif row.Country == 'us|gb|ie' and 'en' in row.language_only:
        return 'en'
    elif row.Country == 'mx' and 'es' in row.language_only:
        return 'es'
    elif row.Country == 'br' and 'pt' in row.language_only:
        return 'pt'
    elif row.Country == 'br' and 'es' in row.language_only:
        return 'es'
    else:
        return row.language_only
    
T['language'] = T.apply(tweet_language, axis=1)

In [13]:
T[['Country', 'language', 'Tweet_stripped']]

Country  \
0      tr       
1      tr       
2      nl       
3      us       
4      us       
5      nl       
6      us       
7      gb       
8      rs       
9      us       
10     mx       
11     ca       
12     my       
13     br       
14     us       
15     br       
16     us       
17     br       
18     id       
19     us       
20     us       
21     us       
22     us       
23     ie       
24     us       
25     us       
26     br       
27     us       
28     us       
29     mx       
30     us       
31     gb       
32     mx       
33     id       
34     mx       
35     id       
36     ca       
37     us       
38     us       
39     tr       
40     us       
41     us       
42     ru       
43     ru       
44     br       
45     us       
46     hu       
47     us       
48     us       
49     us       
50     us       
51     br       
52     my       
53     us       
54     mx       
55     ca       
56     us       
57     id       
58     us       
59     id       
60     br       
61     fr       
62     nl       
63     mx       
64     us       
65     es       
66     br       
67     cl       
68     my       
69     us       
70     br       
71     br       
72     mx       
73     us       
74     id       
75     my       
76     gb       
77     us       
78     us       
79     us       
80     us       
81     us       
82     us       
83     us       
84     nl       
85     rs       
86     us       
87     br       
88     us       
89     br       
90     my       
91     tr       
92     ru       
93     ru       
94     gb       
95     gb       
96     my       
97     id       
98     jp       
99     id       
100    gb       
101    us       
102    nl       
103    nl       
104    us       
105    us       
106    br       
107    br       
108    br       
109    gb       
110    es       
111    cl       
112    jp       
113    us       
114    jp       
115    us       
116    nl       
117    fr       
118    fr       
119    br       
120    us       
121    us       
122    mx       
123    it       
124    jp       
125    ca       
126    us       
127    ca       
128    us       
129    us       
130    us       
131    es       
132    us       
133    cl       
134    es       
135    us       
136    us       
137    gb       
138    us       
139    us       
140    nl       
141    gb       
142    ru       
143    us       
144    id       
145    ca       
146    id       
147    us       
148    br       
149    id       
150    br       
151    us       
152    br       
153    br       
154    us       
155    my       
156    id       
157    gb       
158    cl       
159    mx       
160    ca       
161    us       
162    us       
163    my       
164    my       
165    us       
166    mx       
167    it       
168    us       
169    my       
170    se       
171    it       
172    es       
173    es       
174    us       
175    us       
176    jp       
177    gb       
178    us       
179    us       
180    us       
181    ca       
182    us       
183    br       
184    br       
185    us       
186    us       
187    us       
188    cl       
189    id       
190    us       
191    id       
192    us       
193    id       
194    us       
195    gb       
196    us       
197    us       
198    us       
199    gb       
200    us       
201    us       
202    br       
203    us       
204    mx       
205    br       
206    us       
207    us       
208    us       
209    by       
210    gb       
211    ie       
212    fr       
213    us       
214    us       
215    tr       
216    gb       
217    cl       
218    br       
219    id       
220    br       
221    us       
222    us       
223    tr       
224    us       
225    us       
226    id       
227    es       
228    us       
229    us       
230    us       
231    us       
232    br       
233    us       
234    us  